In [1]:
# load have process qa .json

import json, sys, os, re
from openai import OpenAI
import openai
from tqdm import tqdm
processed_single_qa = json.load(open('/home/zhangyl/videollm-online/data/estp/annotation_train/0/estp.json'))



# gpt key: 


# step 1 : group qa

# step 2: merge multi qa to context qa

In [2]:
import os
print(len(os.listdir('/home/zhangyl/videollm-online/dataset/contextual_qa_single_train_v0_merge/')))

21628


In [3]:
import os
from tqdm import tqdm
output_dir = '/home/zhangyl/videollm-online/dataset/contextual_qa_single_train_v0_merge/'

def timeSatisfy(qa1,qa2):
    last_time = qa1['conversation'][0]['end_time']
    is_satisfy = False
    for conv in qa2['conversation']:
        if conv['end_time'] > last_time:
            is_satisfy = True
            break
    
    return is_satisfy


group_qas = {}
c = 0
for i, video_uid in tqdm(enumerate(processed_single_qa)):
    for clip_uid in processed_single_qa[video_uid]:
        output_prefix = os.path.join(output_dir, f'{video_uid}_{clip_uid}_{i}')
        try:
            group_id = json.load(open(f'{output_prefix}_group.json', 'r'))['groups']
        except:
            continue
        
        # group qa, delete time repeat and number of qa less than 3
        try:
            for group in group_id:
                print(group)
                a_group_qas = []
                for idx in group['question_ids']:
                    if not a_group_qas:
                        a_group_qas.append(processed_single_qa[video_uid][clip_uid][idx])
                        continue
                    if timeSatisfy(a_group_qas[-1], processed_single_qa[video_uid][clip_uid][idx]):
                        a_group_qas.append(processed_single_qa[video_uid][clip_uid][idx])
                
                # print(json.dumps(a_group_qas, indent=4))
                if len(a_group_qas) < 2:
                    continue
                c += 1
                if a_group_qas:
                    if video_uid not in group_qas.keys():
                        group_qas[video_uid] = {}
                    if clip_uid not in group_qas[video_uid].keys():
                        group_qas[video_uid][clip_uid] = []
                    a_group_qas = {
                        'reason': group['reason'],
                        'qas': a_group_qas
                    }
                    group_qas[video_uid][clip_uid].append(a_group_qas)
        except Exception as e:
            print(e)
            continue
    #     break
    # break

print(c)

def sumDict(a):
    c = 0
    for key in a:
        for kk in a[key]:
            c += len(a[key][kk])
    return c

# with open('group_qas.json', 'w') as f:
#     json.dump(group_qas, f, indent=4)
# print(json.dumps(group_qas, indent=4))
print(sumDict(group_qas))
        

103it [00:00, 1026.58it/s]

{'question_ids': [0], 'reason': 'This question is about the specific action of blowing sawdust on the board, which is a distinct task.'}
{'question_ids': [1], 'reason': "This question focuses on the attribute perception of the wooden board's color when it is moved on the jigsaw machine."}
{'question_ids': [2], 'reason': 'This question is about the ego object localization of the compass relative to the user when adjusting it on the board.'}
{'question_ids': [3], 'reason': "This question is about the ego object state change recognition of the board's position when it is placed on the floor."}
{'question_ids': [4], 'reason': 'This question is about object recognition, specifically identifying the red-handled object as a pen.'}
{'question_ids': [5, 7], 'reason': 'These questions are related to the attribute perception and text-rich understanding of the red tube labeled "ACRYLIC GEL".'}
{'question_ids': [6], 'reason': 'This question is about object localization, specifically the position of

313it [00:00, 957.17it/s] 

{'question_ids': [0], 'reason': 'This question is about recognizing the specific action of using the phone, specifically when the user dials the phone.'}
{'question_ids': [0], 'reason': 'This question is about the action of using the phone, which is a specific action related to the phone.'}
{'question_ids': [0], 'reason': 'This question is about the action of looking around, which is a standalone action recognition task.'}
{'question_ids': [1, 2], 'reason': 'These questions are related to the blue plastic bottle on the ground, focusing on its color and its relative location to the white bucket.'}
{'question_ids': [3], 'reason': 'This question is about identifying textual information on the motorcycles, which is a specific text-rich understanding task.'}
{'question_ids': [4], 'reason': 'This question is about locating cleaning equipment, which is a specific object function task.'}
{'question_ids': [5], 'reason': 'This question is about identifying available food for a break, which is a 

500it [00:00, 699.88it/s]

{'question_ids': [0, 1, 3], 'reason': 'These questions are related to the operation and positioning of the phone, focusing on when it is being operated, its category, and its position relative to the user.'}
{'question_ids': [2], 'reason': 'This question is about the color of the backpack when a cup is picked, which is a specific attribute perception task.'}
{'question_ids': [4], 'reason': "This question is about identifying the text on the security personnel's uniform, which is a text-rich understanding task."}
{'question_ids': [5], 'reason': 'This question is about recognizing the object with the red light on the turnstile, which is an object recognition task.'}
{'question_ids': [6, 10], 'reason': 'These questions are related to the caution lines on the stairs and how to safely navigate them, focusing on their color and safety instructions.'}
{'question_ids': [7], 'reason': 'This question is about the proximity of the turnstiles when approaching them, which is an ego object localizat

1141it [00:00, 1479.99it/s]

{'question_ids': [0], 'reason': 'This question is focused on the interactions with the box of foil, including taking and putting it back, which is a specific action sequence.'}
{'question_ids': [1, 2], 'reason': 'These questions are related to the parsnip, specifically its color when taken from the fridge and its location relative to the chopping board when placed on it. They both pertain to attributes and localization of the parsnip.'}
{'question_ids': [0], 'reason': 'This question focuses on the use of the knife during the process, specifically when it is picked up and used for cutting and chopping.'}
{'question_ids': [1], 'reason': 'This question is about the color of the seasoning packet when the food is held, which is a specific attribute perception task.'}
{'question_ids': [2, 5, 7], 'reason': 'These questions are related to the black frying pan, focusing on its location relative to the sink, its color, and its distance from the observer.'}
{'question_ids': [3], 'reason': 'This q

In [4]:
import json

# 样例数据（按照你给出的示例，只是为了演示，不一定包含全部细节）
tasks = [
    {
        "Task Type": " Attribute Perception",
        "question": "Can you remind me of the color of the cloth I use when I wipe the car door?",
        "conversation": [
            {
                "role": "assistant",
                "content": "The cloth you use to wipe the car door is bright orange.",
                "time": 810.4541833333333,
                "start_time": 809.9192838647958,
                "end_time": 810.9890828018707,
                "caption": "The cloth you use to wipe the car door is bright orange."
            },
            {
                "role": "assistant",
                "content": "The cloth you use to wipe the car door is bright orange.",
                "time": 877.0836033333334,
                "start_time": 876.5487038647959,
                "end_time": 877.6185028018708
            },
            {
                "role": "assistant",
                "content": "The cloth you use to wipe the car door is bright orange.",
                "time": 881.6297133333334,
                "start_time": 881.0948138647959,
                "end_time": 882.1646128018708
            }
        ],
        "clip_start_time": 809.9966666666667,
        "clip_end_time": 1064.0963289388021
    },
    {
        "Task Type": " Ego Object Localization",
        "question": "Where is the orange towel positioned relative to me when I spread it on my right hand?",
        "conversation": [
            {
                "role": "assistant",
                "content": "The orange towel is positioned on your right hand, spread across the surface of your palm.",
                "time": 817.0902033333334,
                "start_time": 816.555303864796,
                "end_time": 817.6251028018709
            }
        ],
        "clip_start_time": 809.9966666666667,
        "clip_end_time": 1064.0963289388021
    },
    {
        "Task Type": " Ego Object State Change Recognition",
        "question": "Can you remind me how the towel changes position when I dip it in the water?",
        "conversation": [
            {
                "role": "assistant",
                "content": "The towel is initially held in your right hand, and you dip it into a purple plastic basin filled with water. The towel becomes submerged, absorbing water, and is then lifted out, allowing excess water to drip off.",
                "time": 891.8191133333333,
                "start_time": 891.2842138647959,
                "end_time": 892.3540128018708
            },
            {
                "role": "assistant",
                "content": "The towel is dipped into the water again, causing ripples as it absorbs the water. You hold it under the stream for a few seconds before lifting it back up.",
                "time": 895.6983033333333,
                "start_time": 895.1634038647959,
                "end_time": 896.2332028018708
            },
            {
                "role": "assistant",
                "content": "The towel is removed from the basin, damp and slightly wrung out, before being placed back down beside the basin.",
                "time": 897.3773433333333,
                "start_time": 896.8424438647959,
                "end_time": 897.9122428018708
            },
            {
                "role": "assistant",
                "content": "The towel is squeezed over the basin, releasing water from its fibers as you press on it.",
                "time": 898.3415933333333,
                "start_time": 897.8066938647959,
                "end_time": 898.8764928018708
            }
        ],
        "clip_start_time": 809.9966666666667,
        "clip_end_time": 1064.0963289388021
    },
    {
        "Task Type": "Action Recognition",
        "question": "I want to know when I spray the car or the hand towel. Could you let me know?",
        "time": [
            814.3054633333334,
            818.8428333333334,
            971.5833933333333,
            984.2124633333333,
            1032.4716533333333,
            1061.7254033333334
        ],
        "conversation": [
            {
                "role": "assistant",
                "content": "You spray the hand towel.",
                "time": 814.3054633333334,
                "start_time": 813.7705638647959,
                "end_time": 814.8403628018708
            },
            {
                "role": "assistant",
                "content": "You spray the door.",
                "time": 818.8428333333334,
                "start_time": 818.3079338647959,
                "end_time": 819.3777328018708
            },
            {
                "role": "assistant",
                "content": "You spray the car.",
                "time": 971.5833933333333,
                "start_time": 971.0484938647959,
                "end_time": 972.1182928018708
            },
            {
                "role": "assistant",
                "content": "You spray the hand towel.",
                "time": 984.2124633333333,
                "start_time": 983.6775638647958,
                "end_time": 984.7473628018707
            },
            {
                "role": "assistant",
                "content": "You spray the car.",
                "time": 1032.4716533333333,
                "start_time": 1031.936753864796,
                "end_time": 1033.0065528018706
            },
            {
                "role": "assistant",
                "content": "You spray the hand towel.",
                "time": 1061.7254033333334,
                "start_time": 1061.190503864796,
                "end_time": 1062.2603028018707
            }
        ],
        "clip_start_time": 809.9966666666667,
        "clip_end_time": 1064.0963289388021
    }
]
import random

def merge_conversation_interrupt(tasks):
    """
    将多个任务中的问题和回答按时间合并为一段连续对话，同时实现：
      当新问题插入时（即新的用户提问出现），旧问题后续的回答不再被采纳。
    
    算法步骤：
      1. 遍历所有任务，为每个任务添加一个 task_id，并生成两种消息：
         - 用户提问消息（role 为 "user"），时间戳：
             如果任务中存在 "time" 且是列表，则取列表中第一个时间，否则取第一个回答的时间减去微小偏移量。
         - 助手回答消息（role 为 "assistant"），保持原有的时间戳，同时增加 task_id 字段。
      2. 将所有消息按照时间戳排序。
      3. 遍历排序后的消息，维护一个 current_active_task：
         - 每遇到一个用户提问消息，就更新 current_active_task 为该消息的 task_id。
         - 只有当回答消息的 task_id 与 current_active_task 相同时，该回答才被采纳，否则认为该回答属于已被打断的旧问题而舍弃。
    """
    all_messages = []
    
    # 1. 遍历所有任务，添加消息并附加 task_id
    for task_id, task in enumerate(tasks):

        # 假设 task 为单个任务的字典，修改原始代码：
        
        if task.get("conversation"):
            # 如果任务中没有 "time" 字段，则从 conversation 中提取回答的 "stamp" 时间
            stamps = [msg["time"] for msg in task["conversation"] if "time" in msg]
            if stamps:
                stamps.sort()
                if len(stamps) > 1:
                    idx = random.randint(-1, len(stamps) - 2)
                    if idx == -1:
                        t1 = all_messages[-1]['end_time'] if all_messages else task['clip_start_time']
                    else:
                        t1 = task["conversation"][idx]["end_time"]
                    t2 = task["conversation"][idx+1]['start_time']
                    # question_time = (t1 + t2) / 2.0
                    # 或者：
                    question_time = random.uniform(t1, t2)
                else:
                    t1 = all_messages[-1]['time'] if all_messages else task['clip_start_time']
                    t2 = stamps[0]
                    question_time = random.uniform(t1, t2)
            else:
                continue  # 如果 conversation 中没有时间信息，则跳过该任务
        # elif "time" in task and isinstance(task["time"], list) and task["time"]:
        #     times_list = task["time"]
        #     if len(times_list) > 1:
        #         # 随机选择一个相邻时间对的索引（例如 0 对应第一个和第二个时间，1 对应第二个和第三个时间……）
        #         idx = random.randint(-1, len(times_list) - 2)
        #         if idx == -1:
        #             t1 = all_messages[-1]['time'] if all_messages else task['clip_start_time']
        #         else:
        #             t1 = times_list[idx]
        #         t2 = times_list[idx + 1]
        #         # 这里可以采用平均值作为插入时刻，或者用 random.uniform(t1, t2) 在两者之间随机取值
        #         # question_time = (t1 + t2) / 2.0
        #         # 若需要更随机一点，可以使用下面这行：
        #         question_time = random.uniform(t1, t2)
        #     else:
        #         question_time = times_list[0]
        else:
            continue  # 如果没有任何时间信息，跳过该任务


        
        # 添加用户提问消息，并附上 task_id
        all_messages.append({
            "role": "user",
            "content": task["question"],
            "time": question_time,
            "task_id": task_id
        })
        
        # 添加所有回答消息，并附上 task_id
        for answer in task.get("conversation", []):
            answer_copy = answer.copy()  # 复制字典，避免修改原数据
            answer_copy["task_id"] = task_id
            all_messages.append(answer_copy)
    
    # 2. 按时间戳排序所有消息
    all_messages.sort(key=lambda msg: msg["time"])
    
    # 3. 遍历排序后的消息，并根据“新问题打断旧问题回答”的规则过滤
    filtered_messages = []
    current_active_task = None  # 当前最新的用户提问所属的任务 id
    for msg in all_messages:
        if msg["role"] == "user":
            current_active_task = msg["task_id"]
            filtered_messages.append(msg)
        elif msg["role"] == "assistant":
            # 只有当该回答的 task_id 与当前 active task 相同时，才将其保留
            if msg["task_id"] == current_active_task:
                filtered_messages.append(msg)
            # 否则跳过（这代表该回答属于旧问题，已被新问题打断）
    
    # 4. 如果user下一个不是assistant，删除user
    i = 0
    while i < len(filtered_messages):
        if i == len(filtered_messages) - 1 and filtered_messages[i]['role'] == 'user':
            filtered_messages.pop(i)
        elif filtered_messages[i]['role'] == 'user' and filtered_messages[i+1]['role'] != 'assistant':
            filtered_messages.pop(i)
        else:
            i += 1
    
    for msg in filtered_messages:
        if 'caption' in msg:
            del msg['caption']
        if 'reason' in msg:
            del msg['reason']
    
    return filtered_messages


if __name__ == '__main__':
    merged_conversation = merge_conversation_interrupt(tasks)
    
    # 按时间顺序输出最终的连续对话

    for msg in merged_conversation:
        if 'caption' in msg:
            print(msg['caption'])
        print(f"[{msg['time']:.3f}] {msg['role']}: {msg['content']}")


[878.284] user: Can you remind me of the color of the cloth I use when I wipe the car door?
[881.630] assistant: The cloth you use to wipe the car door is bright orange.
[896.621] user: Can you remind me how the towel changes position when I dip it in the water?
[897.377] assistant: The towel is removed from the basin, damp and slightly wrung out, before being placed back down beside the basin.
[898.342] assistant: The towel is squeezed over the basin, releasing water from its fibers as you press on it.


# step 3 : refine to context qa

In [5]:
from openai import OpenAI
from tqdm import tqdm

# doubao
# def get_llm_reponse_json(system_prompt, user_prompt):
#     client = OpenAI(
#             api_key='',
#             base_url="https://ark.cn-beijing.volces.com/api/v3",
#         )

#     messages = [{"role": "system", "content": system_prompt},
#                 {"role": "user", "content":  user_prompt}]

#     response = client.chat.completions.create(
#         model="ep-20250209171240-27r8g",
#         messages=messages,
#         # response_format={
#         #     'type': 'json_object'
#         # }
#     )
#     return response.choices[0].message.content

def get_llm_reponse_json(system_prompt, user_prompt):
    client = OpenAI(
            api_key="",
            base_url="https://api.deepseek.com",
        )

    messages = [{"role": "system", "content": system_prompt},
                {"role": "user", "content": user_prompt}]

    response = client.chat.completions.create(
        model="deepseek-chat",
        messages=messages,
        # response_format={
        #     'type': 'json_object'
        # }
    )
    return response.choices[0].message.content

system_prompt = open('/home/zhangyl/videollm-online/data/estp/contextual_qa/refine_conv_system_prompt.txt').read()
user_prompt = open('/home/zhangyl/videollm-online/data/estp/contextual_qa/refine_conv_user_prompt.txt').read()
output_dir = '/home/zhangyl/videollm-online/dataset/contextual_qa_single_train_v0_merge_final/'
repeat_num = 1
os.makedirs(output_dir, exist_ok=True)

for video_uid in tqdm(group_qas.keys()):
    for clip_uid in group_qas[video_uid].keys():
        tasks = group_qas[video_uid][clip_uid]
        for i,task in enumerate(tasks):
            for j in range(repeat_num):
            
                if os.path.exists(f'{output_dir}/{video_uid}_{clip_uid}_{i}_{j}.json') and os.path.exists(f'{output_dir}/{video_uid}_{clip_uid}_{i}_{j}.txt'):
                    continue
                try:
                    merged_conversation = merge_conversation_interrupt(task['qas'])
                    prompt = user_prompt.format(task['reason'],json.dumps(merged_conversation, indent=4))
                except:
                    continue

                
                try:
                    answer = get_llm_reponse_json(system_prompt, prompt)
                    answer = json.loads(answer.replace('```','').replace('json','').strip())
                    # answer = None
                except Exception as e:
                    print(e)
                    continue
                
                with open(f'{output_dir}/{video_uid}_{clip_uid}_{i}_{j}.json', 'w') as f:
                    json.dump(answer, f, indent=4)
                with open(f'{output_dir}/{video_uid}_{clip_uid}_{i}_{j}.txt', 'w') as f:
                    f.write(prompt)
            

 45%|████▍     | 279/626 [2:06:05<3:18:29, 34.32s/it]

Expecting ',' delimiter: line 456 column 27 (char 12373)


 76%|███████▌  | 477/626 [10:07:39<7:24:00, 178.79s/it] 

Unterminated string starting at: line 439 column 9 (char 12935)


 92%|█████████▏| 577/626 [16:26:00<3:03:04, 224.18s/it] 

Unterminated string starting at: line 4 column 20 (char 51)


 94%|█████████▍| 591/626 [17:18:02<1:11:46, 123.06s/it]

Expecting value: line 1 column 1 (char 0)


100%|██████████| 626/626 [19:55:32<00:00, 114.59s/it]  


# see QA

In [1]:
# 遍历output_dir,打印videoid，和clipid，然后打印对话，见时间转换成小时分钟秒
import os
import json
from datetime import datetime, timedelta

output_dir = '/home/zhangyl/videollm-online/dataset/contextual_qa_single_v2_final_v2/'

def format_time(seconds):
    # Convert seconds to hours:minutes:seconds format
    time_delta = timedelta(seconds=seconds)
    hours = int(time_delta.total_seconds() // 3600)
    minutes = int((time_delta.total_seconds() % 3600) // 60)
    seconds = time_delta.total_seconds() % 60
    return f"{hours:02d}:{minutes:02d}:{seconds:05.2f}"

# Iterate through files in output directory
for filename in os.listdir(output_dir):
    if filename.endswith('.json'):
        # Extract video_uid and clip_uid from filename
        video_uid, clip_uid, task_id = filename.replace('.json','').split('_')
        
        print(f"\nVideo UID: {video_uid}")
        print(f"Clip UID: {clip_uid}")
        print(f"Task ID: {task_id}")
        print("-" * 50)
        
        # Read and parse JSON file
        with open(os.path.join(output_dir, filename), 'r') as f:
            conversation = json.load(f)
            
        # Print each message in conversation with formatted time
        for message in conversation:
            role = message['role']
            content = message['content']
            time = format_time(message['time'])
            print(f"{role} ({time}): {content}")



Video UID: ffb6dfc1-d2f9-45b1-8e25-2c7d0f32d635
Clip UID: 60c47f37-f81e-4203-b781-850868dcddea
Task ID: 0
--------------------------------------------------
user (00:13:36.37): When do I use the spray during the cleaning process?
assistant (00:13:38.84): You spray the car door.
user (00:14:39.52): What color is the cloth I use for wiping the car door?
assistant (00:14:41.63): The cloth you use is bright orange.
user (00:14:54.23): How does it move when I dip it into the water?
assistant (00:14:55.70): It is submerged, creating ripples as it absorbs water. You hold it under the stream for a few seconds before lifting it back up.
assistant (00:14:57.38): It is then removed from the basin, damp and slightly wrung out, before being placed beside the basin.
assistant (00:14:58.34): You squeeze it over the basin, releasing excess water as you press down.

Video UID: ec41b9e1-dbf9-45c3-bf88-4b250873cad0
Clip UID: d596bc4d-d149-4ca4-8671-630d6303d4de
Task ID: 0
-------------------------------

In [34]:
# Get input from user
text = """
Video UID: ec41b9e1-dbf9-45c3-bf88-4b250873cad0
Clip UID: d596bc4d-d149-4ca4-8671-630d6303d4de
"""

# parser text to video_id, clip_id
# Split text into lines and filter out empty lines
lines = [line for line in text.split('\n') if line.strip()]
# Extract video_id and clip_id from the non-empty lines
video_id = lines[0].split(': ')[1]
clip_id = lines[1].split(': ')[1]

# Find and print matching files
with open('temp.txt', 'w') as out_f:
    pass
for filename in os.listdir(output_dir):
    if filename.startswith(f"{video_id}_{clip_id}_"):
        file_path = os.path.join(output_dir, filename)
        with open('temp.txt', 'a') as out_f:
            out_f.write(f"\nFile: {filename}\n")
            out_f.write("-" * 50 + "\n")
            
            with open(file_path, 'r') as f:
                if filename.endswith('.json'):
                    # Pretty print JSON content
                    content = json.load(f)
                    out_f.write(json.dumps(content, indent=4) + "\n")
                else:
                    # Print text content 
                    out_f.write(f.read() + "\n")
